# PyTerrier demonstration for msmarcov2_passage

This notebook demonstrates retrieval using PyTerrier on the MSMARCO v2 Passage Ranking corpus.

About the corpus: A revised corpus of 138M passages released by Microsoft in July 2021, which should be ranked based on their relevance to questions.  Also used by the TREC 2021 Deep Learning track.

In [1]:

#!pip install -q python-terrier
import pyterrier as pt
if not pt.started():
    pt.init()

from pyterrier.measures import *
dataset = pt.get_dataset('msmarcov2_passage')
        

PyTerrier 0.7.0 has loaded Terrier 5.6 (built by craigmacdonald on 2021-09-17 13:27)


## Systems using index variant terrier_stemmed
Terrier's default Porter stemming, and stopwords removed.

In [2]:
#!pip install git+https://github.com/Georgetown-IR-Lab/OpenNIR.git
import onir_pt
# Lets use a Vanilla BERT ranker from OpenNIR. We'll use the Capreolus model available from Huggingface
vanilla_bert = onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'})

Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex.


In [3]:
bm25_terrier_stemmed = pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_stemmed', wmodel='BM25')

bm25_bert_terrier_stemmed = (
    pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_stemmed') 
    >> pt.text.get_text(pt.get_dataset('irds:msmarco-passage-v2'), 'text') 
    >> onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'}))

dph_terrier_stemmed = pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_stemmed', wmodel='DPH')

dph_bert_terrier_stemmed = (
    pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_stemmed',  wmodel='DPH') 
    >> pt.text.get_text(pt.get_dataset('irds:msmarco-passage-v2'), 'text') 
    >> onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'}))


21:30:20.154 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading lookup file directly from disk (SLOW) - try index.meta.index-source=fileinmem in the index properties file. 1 GiB of memory would be required.
21:30:20.208 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading data file directly from disk (SLOW) - try index.meta.data-source=fileinmem in the index properties file. 8.6 GiB of memory would be required.
21:30:34.314 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading lookup file directly from disk (SLOW) - try index.meta.index-source=fileinmem in the index properties file. 1 GiB of memory would be required.
21:30:34.333 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading data file directly from disk (SLOW) - try index.meta.data-source=fileinmem in the index properties file. 8.6 GiB of memory would be required.
21:30:54.725 [main] WARN org.terrier.s

## Systems using index variant terrier_unstemmed
Terrier index, no stemming, no stopword removal.

In [4]:
#!pip install git+https://github.com/Georgetown-IR-Lab/OpenNIR.git
import onir_pt
# Lets use a Vanilla BERT ranker from OpenNIR. We'll use the Capreolus model available from Huggingface
vanilla_bert = onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'})

In [5]:
bm25_terrier_unstemmed = pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_unstemmed', wmodel='BM25')

bm25_bert_terrier_unstemmed = (
    pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_unstemmed') 
    >> pt.text.get_text(pt.get_dataset('irds:msmarco-passage-v2'), 'text') 
    >> onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'}))

dph_terrier_unstemmed = pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_unstemmed', wmodel='DPH')

dph_bert_terrier_unstemmed = (
    pt.BatchRetrieve.from_dataset('msmarcov2_passage', 'terrier_unstemmed',  wmodel='DPH') 
    >> pt.text.get_text(pt.get_dataset('irds:msmarco-passage-v2'), 'text') 
    >> onir_pt.reranker('hgf4_joint', ranker_config={'model': 'Capreolus/bert-base-msmarco', 'norm': 'softmax-2'}))


21:31:58.787 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading lookup file directly from disk (SLOW) - try index.meta.index-source=fileinmem in the index properties file. 1 GiB of memory would be required.
21:31:58.812 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading data file directly from disk (SLOW) - try index.meta.data-source=fileinmem in the index properties file. 5.7 GiB of memory would be required.
21:32:13.006 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading lookup file directly from disk (SLOW) - try index.meta.index-source=fileinmem in the index properties file. 1 GiB of memory would be required.
21:32:13.029 [main] WARN org.terrier.structures.BaseCompressingMetaIndex - Structure meta reading data file directly from disk (SLOW) - try index.meta.data-source=fileinmem in the index properties file. 5.7 GiB of memory would be required.
21:32:34.051 [main] WARN org.terrier.s

## Evaluation on dev1 topics and qrels
4,552 topics with sparse judgements

In [6]:

pt.Experiment(
    [bm25_terrier_stemmed, bm25_bert_terrier_stemmed, dph_terrier_stemmed, dph_bert_terrier_stemmed, bm25_terrier_unstemmed, bm25_bert_terrier_unstemmed, dph_terrier_unstemmed, dph_bert_terrier_unstemmed],
    pt.get_dataset('msmarcov2_passage').get_topics('dev1'),
    pt.get_dataset('msmarcov2_passage').get_qrels('dev1'),
    batch_size=200,
    filter_by_qrels=True,
    eval_metrics=[RR@10],
    names=['bm25_terrier_stemmed', 'bm25_bert_terrier_stemmed', 'dph_terrier_stemmed', 'dph_bert_terrier_stemmed', 'bm25_terrier_unstemmed', 'bm25_bert_terrier_unstemmed', 'dph_terrier_unstemmed', 'dph_bert_terrier_unstemmed'])
        

21:32:54.584 [main] WARN org.terrier.applications.batchquerying.TRECQuery - trec.encoding is not set; resorting to platform default (ISO-8859-1). Retrieval may be platform dependent. Recommend trec.encoding=UTF-8
config file not found: config
[2021-10-25 22:38:19,897][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-25 22:38:30,939][onir_pt][DEBUG] [starting] batches


[2021-10-25 23:08:15,969][onir_pt][DEBUG] [finished] batches: [29:45] [47918it] [26.84it/s]
[2021-10-25 23:10:30,154][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-25 23:10:30,162][onir_pt][DEBUG] [starting] batches


[2021-10-25 23:41:06,390][onir_pt][DEBUG] [finished] batches: [30:36] [48614it] [26.47it/s]
[2021-10-25 23:43:42,061][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-25 23:43:42,070][onir_pt][DEBUG] [starting] batches


batches:  72%|███████▏  | 35770/50000 [17:34<06:59, 33.93it/s]

[2021-10-26 01:16:46,549][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-26 01:16:46,557][onir_pt][DEBUG] [starting] batches


...

batches:  63%|██████▎   | 31558/50000 [09:58<05:49, 52.80it/s]

[2021-10-29 09:07:56,318][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-29 09:07:56,330][onir_pt][DEBUG] [starting] batches


batches:  46%|████▌     | 22906/50000 [07:06<08:24, 53.78it/s]

[2021-10-29 10:18:30,728][onir_pt][DEBUG] using GPU (deterministic)
[2021-10-29 10:18:30,734][onir_pt][DEBUG] [starting] batches


batches:  75%|███████▌  | 19352/25750 [06:02<01:60, 53.43it/s]